In [2]:
'''
DEGREE ADVERBS (temporal, factual, other)
'''

# temporal = ['never', 'rarely', 'sometimes', 'usually', 'generally', 'often', 'already',  'again',  
#              'constantly',  'repeatedly', 'frequently','always']
# factual = ['maybe',  'perhaps', 'possibly', 'probably', 'really', 'actually', 'literally', 
#            'certainly',  'truly', 'obviously', 'clearly', 'definitely']
# other = ['not', 'almost', 'basically', 'hardly', 'rather', 'quite', 'pretty', 'very',  'especially', 'seriously',
#          'completely', ' extremely'] 
temporal = [' never', 'sometimes', 'usually', 'generally', 'often', 'already', 'frequently','always']
factual = ['maybe',  'perhaps', 'possibly', 'probably', 'really', 'actually', 'certainly', 'definitely']
other = ['not','hardly', 'basically', 'quite', 'pretty', 'very',  'seriously', 'completely'] 

deg_adv = temporal + factual + other

In [166]:
len(deg_adv)

24

In [26]:
# '''
# DEGREE ADVERBS (all extracted)
# '''
# adv_file = '/Users/isabellelorge/Desktop/reddit_data/deg_adv_extracted.txt'
# import re

# adv_all = []

# with open(adv_file) as f:
#     for line in f:
#         adv_all.append(re.sub("[^a-zA-Z]", '', line.strip()))

In [ ]:
# '''
# DEGREE ADVERBS (by intensity)
# '''

# mild = ["a little", 
# "a bit",
# "slightly",
# "somewhat"]

# medium = ["fairly", 
# "pretty", 
# "quite", 
# "rather"]

# # some absolute adv can be used with non gradable adj
# absolute = ["totally",
# "utterly",
# "completely",
# "absolutely",
# "entirely",
# "perfectly",
# "thoroughly"]

# # strong adv are all the other ones 

In [3]:
import spacy

nlp = spacy.load("en_core_web_sm", disable = ['ner', 'parser', 'textcat'])

# doc = nlp('he is really easy.')
# [i.pos_ for i in doc]

In [8]:
'''
Script to decompress commments file, can also be used to loop through comments and do something with them
'''

# import argparse
import re

import pandas as pd

files = ['01', '02', '03', '04', '05', '06', '07', '09', '10', '11', '12']

target_dir = '/Users/isabellelorge/Desktop/reddit_data'

for f in files:
    comments_file = f'{target_dir}/comments_2015-{f}.bz2'
    print(comments_file)

    # def main():

    #     # Read arguments
    #     parser = argparse.ArgumentParser()
    #     parser.add_argument('--comments_file', default=None, type=str, required=True, help='Comments file')
    #     parser.add_argument('--subreddits_file', default=None, type=str, required=False, help='Subreddits file')
    #     parser.add_argument('--target_dir', default=None, type=str, required=False, help='Directory to store comments')
    #     args = parser.parse_args()

    # Read subreddits
    # if subreddits_file:
    #     with open(subreddits_file, 'r') as f:
    #         subreddits = set(f.read().strip().split('\n'))

    if target_dir:
        target_file = '{}/comments_extracted_{}.json'.format(
            target_dir, re.findall(r'\d{4}-\d{2}', comments_file)[0]
        )
        print(target_file)

    # Load comments in chunks, filter for adverbs through string search
    comments = list()
    for c in pd.read_json(comments_file, compression='bz2', lines=True, dtype=False, chunksize=10000):
    #     if subreddits_file:
    #         c = c[c.subreddit.isin(subreddits)]
    
        c = c[c['body'].str.contains(' \w+\.|'.join(deg_adv))]
#         print(len(c))
        comments.append(c)
    
    # concat
    comments = pd.concat(comments, sort=True)
    print(len(comments))
    
    # for each adv, get df containing adv+word+.
    comments_adv = list()
    for adv in deg_adv:
        adv_df = comments[comments['body'].str.contains(f'{adv} \w+\.')]
        
        # get the positions of adv in each comment
        positions = [i for i in enumerate(adv_df['body'].str.find(adv)) if i[1] != -1]
        filtered_positions = []
        
        # for each position, get adverbial expression and check that second word POS is ADJ
        for p in positions:
            try:
                adv_exp = re.findall(f'{adv} \w+\.', adv_df['body'].iloc[p[0]][p[1]:])[0]

                doc_exp = nlp(adv_exp)
                if doc_exp[-2].pos_ == 'ADJ':
#                     print('EXPRESSION:', adv_exp)
#                     print('COMMENT:', adv_df['body'].iloc[p[0]])
                    filtered_positions.append(p[0])
            except Exception as e:
                continue
                
        adv_df_filt = adv_df.iloc[filtered_positions]
        comments_adv.append(adv_df_filt)
    
    # concat
    comments_adv = pd.concat(comments_adv, sort=True)
    
    # Store extracted comments
    comments_adv.to_json(
            target_file,
            orient='records',
            lines=True
        )

    # if __name__ == '__main__':
    # main()


/Users/isabellelorge/Desktop/reddit_data/comments_2015-01.bz2
/Users/isabellelorge/Desktop/reddit_data/comments_extracted_2015-01.json
42513
/Users/isabellelorge/Desktop/reddit_data/comments_2015-02.bz2
/Users/isabellelorge/Desktop/reddit_data/comments_extracted_2015-02.json
39966
/Users/isabellelorge/Desktop/reddit_data/comments_2015-03.bz2
/Users/isabellelorge/Desktop/reddit_data/comments_extracted_2015-03.json
45803
/Users/isabellelorge/Desktop/reddit_data/comments_2015-04.bz2
/Users/isabellelorge/Desktop/reddit_data/comments_extracted_2015-04.json
46832
/Users/isabellelorge/Desktop/reddit_data/comments_2015-05.bz2
/Users/isabellelorge/Desktop/reddit_data/comments_extracted_2015-05.json
50287
/Users/isabellelorge/Desktop/reddit_data/comments_2015-06.bz2
/Users/isabellelorge/Desktop/reddit_data/comments_extracted_2015-06.json
50594
/Users/isabellelorge/Desktop/reddit_data/comments_2015-07.bz2
/Users/isabellelorge/Desktop/reddit_data/comments_extracted_2015-07.json
59781
/Users/isabel

In [9]:
'''
Getting comments from decompressed file and creating dataframe (just for eyeballing,
prob more efficient to work with json?)
'''
import pandas as pd
import json

dfs = []
files = ['01', '02', '03', '04', '05', '06', '07', '09', '10', '11', '12']

for f in files:
    print(f)
    comments_file = f'/Users/isabellelorge/Desktop/reddit_data/comments_extracted_2015-{f}.json'

    comments = []

    with open(comments_file) as f:
        for line in f:
            comment = json.loads(line)
            comments.append(comment)

    df = pd.DataFrame(comments)
    dfs.append(df)

final_df = pd.concat(dfs, sort=True)

01
02
03
04
05
06
07
09
10
11
12


In [11]:
adv_adj = {}
import re

for adv in deg_adv:
    print(adv)
    adv_df = final_df[final_df['body'].str.contains(f'{adv} \w+\.')]

    # get the positions of adv in each comment
    positions = [i for i in enumerate(adv_df['body'].str.find(adv)) if i[1] != -1]

    # for each position, get adverbial expression and check that second word POS is ADJ
    for p in positions:
            adv_exp = re.findall(f'{adv} \w+\.', adv_df['body'].iloc[p[0]][p[1]:])[0]
#             print(adv_exp)
            adj = re.sub('\.', '', adv_exp.split()[1])
       
            doc_exp = nlp(adv_exp)
            if doc_exp[-2].pos_ == 'ADJ':
#                 print(adj)
                if adv in adv_adj:
                    adv_adj[adv]['count']+= 1
#                     print(adv_adj[adv]['adj'])
                    
                    if adj in adv_adj[adv]['adj']:
                        adv_adj[adv]['adj'][adj] += 1
                    else:
                        adv_adj[adv]['adj'][adj] = 1
                else:
                    adv_adj[adv] = {'count' : 1, 'adj' : {}}

 never
sometimes
usually
generally
often
already
frequently
always
maybe
perhaps
possibly
probably
really
actually
certainly
definitely
not
hardly
basically
quite
pretty
very
seriously
completely


In [14]:
[(k, adv_adj[k]['count']) for k in adv_adj]

[(' never', 1342),
 ('sometimes', 450),
 ('usually', 763),
 ('generally', 1182),
 ('often', 1058),
 ('already', 2436),
 ('frequently', 84),
 ('always', 4434),
 ('maybe', 306),
 ('perhaps', 111),
 ('possibly', 332),
 ('probably', 2200),
 ('really', 16860),
 ('actually', 7087),
 ('certainly', 1373),
 ('definitely', 1810),
 ('not', 79023),
 ('hardly', 1336),
 ('basically', 1122),
 ('quite', 12867),
 ('pretty', 31386),
 ('very', 49689),
 ('seriously', 713),
 ('completely', 16824)]

In [16]:
adv_adj['very']

{'count': 49689,
 'adj': {'low': 763,
  'dangerous': 388,
  'simple': 582,
  'bright': 151,
  'post': 155,
  'sick': 43,
  'relevant': 311,
  'different': 1830,
  'effective': 445,
  'bad': 425,
  'frustrating': 123,
  'true': 944,
  'popular': 325,
  'complex': 107,
  'interesting': 1299,
  'difficult': 584,
  'angry': 114,
  'dumb': 46,
  'shortcoming': 2,
  'valuable': 115,
  'important': 1102,
  'unlikely': 364,
  'little': 1020,
  'weak': 209,
  'concrete': 8,
  'expensive': 447,
  'good': 1164,
  'progressive': 125,
  'tolerant': 20,
  'problematic': 79,
  'least': 1032,
  'unconstitutional': 8,
  'overgrazed': 2,
  'debatable': 38,
  'serious': 159,
  'informative': 228,
  'immature': 28,
  'clear': 736,
  'illegal': 73,
  'confused': 197,
  'destabilizing': 3,
  'wealthy': 279,
  'similar': 607,
  'worrying': 36,
  'unreliable': 28,
  'happy': 219,
  'substantive': 19,
  'rare': 312,
  'imperfect': 5,
  'leery': 3,
  'untrue': 17,
  'convenient': 43,
  'naive': 165,
  'possible

In [18]:
# final_df.to_csv('/Users/isabellelorge/Desktop/df_final.csv')

In [19]:
# with open('/Users/isabellelorge/Desktop/adjectives.json', 'w') as fp:
#     json.dump(adv_adj, fp)

In [85]:
'''
Creating a big string to parse (better to work with json..?)
'''
# body = " ".join([b for b in df['body'].iloc[1000]])

In [88]:
'''
Length for batches
'''
# len(df)//1000

664

In [5]:
import stanza
stanza.download('en')
nlp = stanza.Pipeline('en', processors = 'tokenize, pos, lemma, depparse')

2022-05-04 22:33:58 INFO: Downloading default packages for language: en (English)...
2022-05-04 22:34:01 INFO: File exists: /Users/isabellelorge/stanza_resources/en/default.zip.
2022-05-04 22:34:06 INFO: Finished downloading models and saved to /Users/isabellelorge/stanza_resources.
2022-05-04 22:34:06 INFO: Loading these models for language: en (English):
| Processor | Package  |
------------------------
| tokenize  | combined |
| pos       | combined |
| lemma     | combined |
| depparse  | combined |

2022-05-04 22:34:06 INFO: Use device: cpu
2022-05-04 22:34:06 INFO: Loading: tokenize
2022-05-04 22:34:06 INFO: Loading: pos
2022-05-04 22:34:06 INFO: Loading: lemma
2022-05-04 22:34:07 INFO: Loading: depparse
2022-05-04 22:34:08 INFO: Done loading processors!


In [13]:
'''
Loop batches of comments, parse with stanza to find ADV+ADJ constructions and extract ADV
'''


# adv_dict = {}

for i in range(137,(len(df)//1000)+1):
    print(i)
    
    # if it's the last batch
    if i == len(df)//1000+1:
        start = i*1000
        body = " ".join([b for b in df['body'].iloc[start:]])
    else:
        start = i*1000
        end = start + 1000
        print(start, end)
        body = " ".join([b for b in df['body'].iloc[start:end]])
        
    doc = nlp(body)
    for sentence in doc.sentences:
        for word in sentence.words:
            POS = word.upos
            lemma = word.lemma
            # get the relevant dependency and filter through that 
#             (BUT AFTER REDUCING DATASET TO COMMENT WITH relevant adv?)

            if POS=='ADV':

                # if the lemma is already in our dict
                if lemma in adv_dict:
                    adv_dict[lemma] += 1

                else:
                    adv_dict[lemma] = 1

In [98]:
'''
Sort adv by reverse frequency order
'''
# {k: v for k, v in sorted(adv_dict.items(), key=lambda item: item[1], reverse=True)}

{'so': 32345,
 'just': 31732,
 'even': 16537,
 'then': 15851,
 'also': 13223,
 'really': 12833,
 'only': 12069,
 'more': 11748,
 'now': 11126,
 'here': 10835,
 'as': 10673,
 'still': 9579,
 'very': 9542,
 'actually': 9301,
 'too': 7903,
 'why': 7790,
 'never': 7587,
 'well': 7033,
 'how': 6402,
 'much': 6177,
 'pretty': 5588,
 'back': 5265,
 'there': 5210,
 'already': 4890,
 'at': 4876,
 'probably': 4857,
 'most': 4635,
 'always': 4613,
 'right': 4593,
 'far': 4497,
 'again': 4412,
 'maybe': 4352,
 'ever': 4143,
 'all': 3999,
 'rather': 3886,
 'however': 3747,
 'though': 3529,
 'least': 3523,
 'simply': 3502,
 'instead': 3353,
 'of': 3149,
 'exactly': 3117,
 'completely': 2854,
 'almost': 2749,
 'course': 2647,
 'away': 2542,
 'long': 2424,
 'less': 2415,
 'often': 2394,
 'over': 2346,
 'especially': 2277,
 'basically': 2219,
 'ago': 2196,
 'certainly': 2094,
 'about': 2043,
 'obviously': 2015,
 'literally': 2007,
 'around': 1984,
 'absolutely': 1981,
 'first': 1927,
 'clearly': 1922,


In [99]:
'''
Store just in case
'''
# with open('adv_dict3.json', 'w') as fp:
#     json.dump(adv_dict, fp)

In [1]:
'''
Retrieve extracted adv
'''
# import json
# j = '/Users/isabellelorge/Desktop/reddit_project/adv_dict3.json'
# with open(j, 'r') as f:
#     adv_dict = json.load(f)

In [2]:
len(adv_dict)

3524

In [6]:
def get_head_pos(word, sentence):
    head_poss = {}
    for w in sentence.words:
        if w.lemma == word:
            head_char = w.misc
            head_id = w.head -1
            head_text = sentence.tokens[head_id].to_dict()[0]['lemma']
            head_pos = sentence.tokens[head_id].to_dict()[0]['upos']
            head_poss[head_char] = head_pos
    return head_pos, head_text


In [319]:
# tokenizer = stanza.Pipeline('en', processors='tokenize')

In [20]:
'''
Loop through comments in df, find target adv with ADV+ADJ (adj as head)
'''

import re
# advs_sentences = {}
filtered_adj = ['much', 'least', 'many']
# advs = {}
# adv_counts = {}


for i, s in df['body'].iloc[28344:].iteritems():
    print(i)
    if i == 100000:
        with open('advs_sentences_new2.json', 'w') as fp:
            json.dump(advs_sentences, fp)
    adv = {}
    # could just look around the relevant span..?
    # this may be extremely inefficient
    for word in deg_adv:
        if [i.span() for i in re.finditer(word, s)]:
            adv[word] = [i.span() for i in re.finditer(word, s)]

    if any([a not in adv_counts for a in adv]) or any([len(adv_counts[a]) < 15 for a in adv]):
#         doc = tokenizer(s)
        doc = nlp(s)
        for s_i, sentence in enumerate(doc.sentences):
            words = [word.text for word in sentence.words]
            for adv in deg_adv:
                process = False
                if adv not in adv_counts:
                    process = True
                else:
                    if len(adv_counts[adv]) < 15:
                        process = True
                if adv in words and process == True:
                    adv_idx = words.index(adv)
                    pos, text = get_head_pos(adv, sentence)
                    try:
                        if pos =='ADJ' and text not in filtered_adj and words[adv_idx+1] == text:
                            print(adv, text)
    #                         print(sentence.text)

                            # if we have combination already, add to examples
                            if doc.sentences[s_i -1]:
                                if adv + '_' + text in advs_sentences:
                                    advs_sentences[adv + '_' + text]['count']+=1
                                    advs_sentences[adv + '_' + text]['sentences'].append(doc.sentences[s_i -1].text
                                                                                         + ' ' + sentence.text)
                                else:
                                    advs_sentences[adv + '_' + text] = {'count' :1, 'sentences': 
                                                                        [doc.sentences[s_i -1].text  
                                                                         + ' ' + sentence.text]}

                                # count adv and adj occurrences

                                if adv in adv_counts:
                                    if text in adv_counts[adv]:
                                        adv_counts[adv][text] += 1
                                    else:
                                        adv_counts[adv][text] = 1
                                else:
                                    adv_counts[adv] = {text: 1}
                    except IndexError:
                        continue


28344
28345
28346
28347
28348
28349
28350
28351
28352
28353
28354
28355
28356
28357
28358
28359
28360
28361
28362
28363
28364
28365
28366
28367
28368
28369
28370
28371
28372
28373
28374
28375
28376
28377
28378
28379
28380
28381
28382
28383
28384
28385
28386
28387
28388
28389
28390
28391
28392
28393
28394
28395
28396
28397
28398
28399
28400
28401
28402
28403
28404
28405
28406
28407
28408
28409
28410
28411
28412
28413
28414
28415
28416
28417
28418
28419
28420
28421
28422
28423
28424
28425
28426
28427
28428
28429
28430
28431
28432
28433
28434
28435
28436
28437
possibly interesting
28438
28439
28440
28441
28442
28443
28444
28445
28446
28447
28448
28449
28450
28451
28452
28453
28454
28455
28456
28457
28458
28459
28460
28461
28462
28463
28464
28465
28466
28467
28468
28469
28470
28471
28472
28473
28474
28475
28476
28477
28478
28479
28480
28481
28482
28483
28484
28485
28486
28487
28488
28489
28490
28491
28492
28493
28494
28495
28496
28497
28498
28499
28500
28501
28502
28503
28504
28505
28506
2

maybe more
29706
29707
29708
29709
29710
29711
29712
29713
29714
29715
29716
29717
29718
29719
29720
29721
29722
29723
29724
29725
29726
29727
29728
29729
29730
29731
29732
29733
29734
29735
29736
29737
29738
29739
29740
29741
29742
29743
29744
29745
29746
29747
29748
29749
29750
29751
29752
29753
29754
29755
29756
29757
29758
29759
29760
29761
29762
29763
29764
29765
29766
29767
29768
29769
29770
29771
29772
29773
29774
29775
29776
29777
29778
29779
29780
29781
29782
29783
29784
29785
29786
29787
29788
29789
29790
29791
29792
29793
29794
29795
29796
29797
29798
29799
29800
29801
29802
29803
29804
29805
29806
29807
29808
29809
29810
29811
29812
29813
29814
29815
29816
29817
29818
29819
29820
29821
29822
29823
29824
29825
29826
29827
29828
29829
29830
29831
29832
29833
29834
29835
29836
29837
29838
29839
29840
29841
29842
29843
29844
29845
29846
29847
29848
29849
29850
29851
29852
29853
29854
29855
29856
29857
29858
29859
29860
29861
29862
29863
29864
29865
29866
29867
29868
29869
29870

31060
31061
31062
31063
31064
31065
31066
31067
31068
31069
31070
31071
31072
31073
31074
31075
31076
31077
31078
31079
31080
31081
31082
31083
31084
31085
31086
31087
31088
31089
31090
31091
31092
31093
31094
31095
31096
31097
31098
31099
31100
31101
31102
31103
31104
31105
31106
31107
31108
31109
31110
31111
31112
31113
31114
31115
31116
31117
31118
31119
31120
31121
31122
31123
31124
31125
31126
31127
31128
31129
31130
31131
31132
31133
31134
31135
31136
31137
31138
31139
31140
31141
31142
31143
31144
31145
31146
31147
31148
31149
31150
31151
31152
31153
31154
31155
31156
31157
31158
31159
31160
31161
31162
31163
31164
31165
31166
31167
31168
31169
31170
31171
31172
31173
31174
31175
31176
31177
31178
31179
31180
31181
31182
31183
31184
31185
31186
31187
31188
31189
31190
31191
31192
31193
31194
31195
31196
31197
31198
31199
31200
31201
31202
31203
31204
31205
31206
31207
31208
31209
31210
31211
31212
31213
31214
31215
31216
31217
31218
31219
31220
31221
31222
31223
31224
31225
3122

32432
32433
32434
32435
32436
32437
32438
32439
32440
32441
32442
32443
32444
32445
32446
32447
32448
32449
32450
32451
32452
32453
32454
32455
32456
32457
32458
32459
32460
32461
32462
32463
32464
32465
32466
32467
32468
32469
32470
32471
32472
32473
32474
32475
32476
32477
32478
32479
32480
32481
32482
32483
32484
32485
32486
32487
32488
32489
32490
32491
32492
32493
32494
32495
32496
32497
32498
32499
32500
32501
32502
32503
32504
32505
32506
32507
32508
32509
32510
32511
32512
32513
32514
32515
32516
32517
32518
32519
32520
32521
32522
32523
32524
32525
32526
32527
32528
32529
32530
32531
32532
32533
32534
32535
32536
32537
32538
32539
32540
32541
32542
32543
32544
32545
32546
32547
32548
32549
32550
32551
32552
32553
32554
32555
32556
32557
32558
32559
32560
32561
32562
32563
32564
32565
32566
32567
32568
32569
32570
32571
32572
32573
32574
32575
32576
32577
32578
32579
32580
32581
32582
32583
32584
32585
32586
32587
32588
32589
32590
32591
32592
32593
32594
32595
32596
32597
3259

33783
33784
33785
33786
33787
33788
33789
33790
33791
33792
33793
33794
33795
33796
33797
33798
33799
33800
33801
33802
33803
33804
33805
33806
33807
33808
33809
33810
33811
33812
33813
33814
33815
33816
33817
33818
33819
33820
33821
33822
33823
33824
33825
33826
33827
33828
33829
33830
33831
33832
33833
33834
33835
33836
33837
33838
33839
33840
33841
33842
33843
33844
33845
33846
33847
33848
33849
33850
33851
33852
33853
33854
33855
33856
33857
33858
33859
33860
33861
33862
33863
33864
33865
33866
33867
33868
33869
33870
33871
33872
33873
33874
33875
33876
33877
33878
33879
33880
33881
33882
33883
33884
33885
33886
33887
33888
33889
33890
33891
33892
33893
33894
33895
33896
33897
33898
33899
33900
33901
33902
33903
33904
33905
33906
33907
33908
33909
33910
33911
33912
33913
33914
33915
33916
33917
33918
33919
33920
33921
33922
33923
33924
33925
33926
33927
33928
33929
33930
33931
33932
33933
33934
33935
33936
33937
33938
33939
33940
33941
33942
33943
33944
33945
33946
33947
33948
3394

...

129415
129416
129417
129418
129419
129420
129421
129422
129423
129424
129425
129426
129427
129428
129429
129430
129431
129432
129433
129434
129435
129436
129437
129438
129439
129440
129441
129442
129443
129444
129445
129446
129447
129448
129449
129450
129451
129452
129453
129454
129455
129456
129457
129458
129459
129460
129461
129462
129463
129464
129465
129466
129467
129468
129469
129470
129471
129472
129473
129474
129475
129476
129477
129478
129479
129480
129481
129482
129483
129484
129485
129486
129487
129488
129489
129490
129491
129492
129493
129494
129495
129496
129497
129498
129499
129500
129501
129502
129503
129504
129505
129506
129507
129508
129509
129510
129511
129512
129513
129514
129515
129516
129517
129518
129519
129520
129521
129522
129523
129524
129525
129526
129527
129528
129529
129530
129531
129532
129533
129534
129535
129536
129537
129538
129539
129540
129541
129542
129543
129544
129545
129546
129547
129548
129549
129550
129551
129552
129553
129554
129555
129556
129557

130591
130592
130593
130594
130595
130596
130597
130598
130599
130600
130601
130602
130603
130604
130605
130606
130607
130608
130609
130610
130611
130612
130613
130614
130615
130616
130617
130618
130619
130620
130621
130622
130623
130624
130625
130626
130627
130628
130629
130630
130631
130632
130633
130634
130635
130636
130637
130638
130639
130640
130641
130642
130643
130644
130645
130646
130647
130648
130649
130650
130651
130652
130653
130654
130655
130656
130657
130658
130659
130660
130661
130662
130663
130664
130665
130666
130667
130668
130669
130670
130671
130672
130673
130674
130675
130676
130677
130678
130679
130680
130681
130682
130683
130684
130685
130686
130687
130688
130689
130690
130691
130692
130693
130694
130695
130696
130697
130698
130699
130700
130701
130702
130703
130704
130705
130706
130707
130708
130709
130710
130711
130712
130713
130714
130715
130716
130717
130718
130719
130720
130721
130722
130723
130724
130725
130726
130727
130728
130729
130730
130731
130732
130733

131789
131790
131791
131792
131793
131794
131795
131796
131797
131798
131799
131800
131801
131802
131803
131804
131805
131806
131807
131808
131809
131810
131811
131812
131813
131814
131815
131816
131817
131818
131819
131820
131821
131822
131823
131824
131825
131826
131827
131828
131829
131830
131831
131832
131833
131834
131835
131836
131837
131838
131839
131840
131841
131842
131843
131844
131845
131846
131847
131848
131849
131850
131851
131852
131853
131854
131855
131856
131857
131858
131859
131860
131861
131862
131863
131864
131865
131866
131867
131868
131869
131870
131871
131872
131873
131874
131875
131876
131877
131878
131879
131880
131881
131882
131883
131884
131885
131886
131887
131888
131889
131890
131891
131892
131893
131894
131895
131896
131897
131898
131899
131900
131901
131902
131903
131904
131905
131906
131907
131908
131909
131910
131911
131912
131913
131914
131915
131916
131917
131918
131919
131920
131921
131922
131923
131924
131925
131926
131927
131928
131929
131930
131931

132970
132971
132972
132973
132974
132975
132976
132977
132978
132979
132980
132981
132982
132983
132984
132985
132986
132987
132988
132989
132990
132991
132992
132993
132994
132995
132996
132997
132998
132999
133000
133001
133002
133003
133004
133005
133006
133007
133008
133009
133010
133011
133012
133013
133014
133015
133016
133017
133018
133019
133020
133021
133022
133023
133024
133025
133026
133027
133028
133029
133030
133031
133032
133033
133034
133035
133036
133037
133038
133039
133040
133041
133042
133043
133044
133045
133046
133047
133048
133049
133050
133051
133052
133053
133054
133055
133056
133057
133058
133059
133060
133061
133062
133063
133064
133065
133066
133067
133068
133069
133070
133071
133072
133073
133074
133075
133076
133077
133078
133079
133080
133081
133082
133083
133084
133085
133086
133087
133088
133089
133090
133091
133092
133093
133094
133095
133096
133097
133098
133099
133100
133101
133102
133103
133104
133105
133106
133107
133108
133109
133110
133111
133112

KeyboardInterrupt: 

In [30]:
# can try and pick the last ones by hand just doing a string search..?
[(k, len(adv_counts[k])) for k in adv_counts if len(adv_counts[k]) < 15]

[('frequently', 13),
 ('rarely', 10),
 ('again', 7),
 ('constantly', 7),
 ('repeatedly', 1)]

In [26]:
sent_json = '/Users/isabellelorge/Desktop/reddit_project/advs_sentences_new3.json'
with open(sent_json, 'r') as f:
    adv_sent_json = json.load(f)

In [28]:
len(adv_sent_json)

488

In [68]:
# remove: sentences with links, sentences < 3 words, duplicates. Then see what remains
# new_adv_sent = {}
# idx = 0
# for k in adv_sent_json:
#     print(idx)
#     adv = adv_sent_json[k]
#     for s in adv['sentences']:
#         processed_doc = nlp(s)
# #         print(processed_doc.sentences)
#         sentences = [s for i, s in enumerate(processed_doc.sentences)]
#         if len(sentences) == 2:
#             s1_words = [word.text for word in sentences[0].words]
#             s2_words = [word.text for word in sentences[1].words]
#             k_adv = k.split('_')[0]
#             k_adv_idx = s2_words.index(k_adv)
#             previous = s2_words[k_adv_idx-1]
#     #         print(s1_words)
#     #         print(s1_words, s2_words)

#             if not('http://' in s or len(first_sent.words) < 3 or s1_words == s2_words) or previous == 'not':
#                 if k not in new_adv_sent:
#                      new_adv_sent[k] = [s]
#                 else:
#                     new_adv_sent[k].append(s)
#     idx+=1


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [111]:
counts = {}
len(new_adv_sent)

for a in deg_adv:
    print(a)
    for k in adv_sent_json:
        print(k)
        if k.split('_')[0] == a:
            print('yes')
            if a not in counts:
                counts[a] =1
            else:
                counts[a] +=1


never
probably_right
really_nice
quite_grateful
pretty_expensive
not_convinced
pretty_nice
pretty_generous
usually_civil
pretty_dangerous
not_okay
pretty_common
not_economic
completely_conservative
truly_wonderful
pretty_silly
completely_different
very_contemptuous
very_enamored
pretty_upset
not_acceptable
very_important
very_lucky
completely_separate
pretty_simple
really_brutal
pretty_successful
completely_salient
never_able
yes
very_poor
pretty_despicable
maybe_more
pretty_angry
really_angry
not_alone
always_true
not_fair
not_new
not_sure
not_possible
rather_damning
seriously_itchy
not_appropriate
very_bad
quite_sure
really_sorry
not_hard
completely_incompatible
not_preposterous
rather_bad
very_wealthy
not_enough
very_strong
very_basic
very_smart
really_worried
hardly_surprising
very_large
really_probable
very_minimal
completely_uninsured
quite_obvious
really_solar
often_more
actually_pointless
probably_higher
literally_evil
basically_nonsense
really_hardcore
completely_right
complet

certainly_worth
rather_bizarre
never_good
rather_physcotic
obviously_clueless
rather_meaningful
rather_functional
always_able
basically_dead
rather_significant
frequently_fatal
truly_socialist
already_overcrowded
probably_illegal
basically_capitalist
truly_different
clearly_derogatory
truly_great
always_amazed
already_porous
possibly_undermedicated
especially_wary
especially_socialist
obviously_libertarian
seriously_flawed
usually_right
yes
clearly_anti-woman
definitely_effective
literally_antithetical
sometimes_necessary
usually_annoying
yes
hardly_socialist
already_difficult
always_worth
certainly_concerned
almost_hysterical
clearly_anti-feminist
actually_illegal
usually_wrong
yes
often_foreign
probably_better
especially_present
often_scarce
definitely_involved
certainly_relevant
almost_black
never_fair
already_fine
sometimes_inaccessible
clearly_overworked
generally_corrupt
perhaps_worse
sometimes_orthodox
often_lazy
truly_fair
probably_neutral
definitely_interesting
almost_free
tru

possibly_social
clearly_reactionary
possibly_catastrophic
never_appropriate
never_happy
sometimes_murky
usually_comparable
certainly_able
hardly_immoral
sometimes_ideological
clearly_legal
possibly_interesting
hardly_enough
clearly_rich
never_popular
hardly_perfect
literally_painful
usually_related
usually_curious
basically_different
never_acceptable
basically_obsolete
certainly_present
hardly_new
definitely_right
rarely_popular
sometimes_worse
possibly_true
certainly_unrelated
constantly_short
maybe_true
possibly_dangerous
seriously_disappointing
definitely_better
definitely_full
basically_negative
seriously_faulty
perhaps_more
rarely_chronic
seriously_distraught
rarely_unnecessary
definitely_wrong
definitely_lesser
basically_interchangeable
perhaps_simpler
seriously_nonsensical
basically_ambivalent
perhaps_unfounded
maybe_misleading
literally_responsible
constantly_blameless
possibly_problematic
basically_unavoidable
perhaps_unfortunate
seriously_dumb
maybe_possible
frequently_fascin

certainly_cruel
certainly_poor
truly_concerned
literally_lower
already_predisposed
generally_larger
especially_healthy
generally_curious
completely_uncalibrated
completely_irrational
literally_astounding
almost_pointless
literally_impossible
almost_zero
especially_true
quite_lazy
almost_overwhelming
really_useful
actually_available
always_wrong
really_worth
really_sure
truly_smart
often_enough
always_harmful
generally_popular
almost_total
completely_irrelevant
almost_apologetic
definitely_responsible
possibly_equivalent
truly_dangerous
quite_simple
always_easy
obviously_dense
almost_pacifistic
seriously_misinformed
actually_worse
obviously_one-sided
definitely_possible
rather_anti-libertarian
seriously_overcrowded
quite_good
hardly_fair
maybe_unsustainable
probably_closer
truly_new
actually_curious
completely_immoral
usually_negative
actually_homophobic
actually_able
clearly_racist
sometimes_stupid
quite_positive
hardly_liberal
rather_small
certainly_constitutional
almost_impossible
al

probably_better
especially_present
often_scarce
definitely_involved
certainly_relevant
almost_black
never_fair
already_fine
sometimes_inaccessible
clearly_overworked
generally_corrupt
perhaps_worse
yes
sometimes_orthodox
often_lazy
truly_fair
probably_neutral
definitely_interesting
almost_free
truly_free
probably_bigger
maybe_half
truly_non-lethal
rarely_valid
frequently_innocuous
clearly_better
often_difficult
never_likely
hardly_homogeneous
obviously_incorrect
sometimes_nonsensical
clearly_minor
probably_good
generally_sympathetic
obviously_unrelated
never_enough
especially_pernicious
usually_black
already_wealthy
already_competitive
literally_worse
truly_uneducated
usually_free
already_underway
especially_critical
never_worth
obviously_dead
already_familiar
literally_zero
already_higher
probably_fine
rarely_true
generally_true
generally_anti-austerity
never_afraid
generally_liberal
certainly_socialist
clearly_cheaper
often_bad
sometimes_disarray
hardly_limited
basically_unheard
basi

...

quite_lazy
almost_overwhelming
really_useful
actually_available
always_wrong
really_worth
really_sure
truly_smart
yes
often_enough
always_harmful
generally_popular
almost_total
completely_irrelevant
almost_apologetic
definitely_responsible
possibly_equivalent
truly_dangerous
yes
quite_simple
always_easy
obviously_dense
almost_pacifistic
seriously_misinformed
actually_worse
obviously_one-sided
definitely_possible
rather_anti-libertarian
seriously_overcrowded
quite_good
hardly_fair
maybe_unsustainable
probably_closer
truly_new
yes
actually_curious
completely_immoral
usually_negative
actually_homophobic
actually_able
clearly_racist
sometimes_stupid
quite_positive
hardly_liberal
rather_small
certainly_constitutional
almost_impossible
already_able
especially_vulnerable
quite_right
obviously_far
actually_less
quite_obsolete
obviously_poor
possibly_horrendous
probably_best
seriously_ill
generally_egalitarian
quite_apolitical
especially_important
truly_afraid
yes
clearly_demonstrable
always_ha

perhaps_worse
sometimes_orthodox
often_lazy
truly_fair
probably_neutral
definitely_interesting
yes
almost_free
truly_free
probably_bigger
maybe_half
truly_non-lethal
rarely_valid
frequently_innocuous
clearly_better
often_difficult
never_likely
hardly_homogeneous
obviously_incorrect
sometimes_nonsensical
clearly_minor
probably_good
generally_sympathetic
obviously_unrelated
never_enough
especially_pernicious
usually_black
already_wealthy
already_competitive
literally_worse
truly_uneducated
usually_free
already_underway
especially_critical
never_worth
obviously_dead
already_familiar
literally_zero
already_higher
probably_fine
rarely_true
generally_true
generally_anti-austerity
never_afraid
generally_liberal
certainly_socialist
clearly_cheaper
often_bad
sometimes_disarray
hardly_limited
basically_unheard
basically_dribble
already_illegal
never_captive
maybe_less
generally_impolite
probably_ineligible
sometimes_little
literally_illegal
often_best
hardly_revolutionary
often_ineffective
perha

yes
perhaps_unfortunate
seriously_dumb
maybe_possible
frequently_fascinating
possibly_regional
possibly_depressed
literally_unheard
frequently_enough
perhaps_fluffy
literally_delusional
frequently_wrong
perhaps_retired
perhaps_related
perhaps_hypocritical
frequently_impossible
perhaps_excessive
rarely_fatal
maybe_naive
perhaps_inconclusive
again_young
again_bored
frequently_rich
possibly_contentious
maybe_other
constantly_combative
perhaps_better
frequently_wealthy
frequently_incorrect
constantly_amazed
maybe_semi-related
repeatedly_condescending
maybe_religious
frequently_corrupt
again_flattered
frequently_worthless
frequently_good
constantly_cold
maybe_real
frequently_structural
rarely_deadly
rarely_objective
again_simple
rarely_constructive
constantly_surprised
repeatedly_enough
repeatedly_wrong
repeatedly_supportive
repeatedly_true
hardly
probably_right
really_nice
quite_grateful
pretty_expensive
not_convinced
pretty_nice
pretty_generous
usually_civil
pretty_dangerous
not_okay
pret

really_sure
truly_smart
often_enough
always_harmful
generally_popular
almost_total
completely_irrelevant
almost_apologetic
definitely_responsible
possibly_equivalent
truly_dangerous
quite_simple
always_easy
obviously_dense
almost_pacifistic
seriously_misinformed
actually_worse
obviously_one-sided
definitely_possible
rather_anti-libertarian
seriously_overcrowded
quite_good
hardly_fair
maybe_unsustainable
probably_closer
truly_new
actually_curious
completely_immoral
usually_negative
actually_homophobic
actually_able
clearly_racist
sometimes_stupid
quite_positive
hardly_liberal
rather_small
certainly_constitutional
almost_impossible
already_able
especially_vulnerable
quite_right
obviously_far
actually_less
quite_obsolete
obviously_poor
possibly_horrendous
probably_best
seriously_ill
generally_egalitarian
quite_apolitical
especially_important
truly_afraid
clearly_demonstrable
always_happy
always_voluntary
rather_hypocritical
almost_complete
basically_worried
quite_convinced
obviously_pro-g

generally_sympathetic
obviously_unrelated
never_enough
especially_pernicious
usually_black
already_wealthy
already_competitive
literally_worse
truly_uneducated
usually_free
already_underway
especially_critical
never_worth
obviously_dead
already_familiar
literally_zero
already_higher
probably_fine
rarely_true
generally_true
generally_anti-austerity
never_afraid
generally_liberal
certainly_socialist
clearly_cheaper
often_bad
sometimes_disarray
hardly_limited
basically_unheard
basically_dribble
already_illegal
never_captive
maybe_less
generally_impolite
probably_ineligible
sometimes_little
literally_illegal
often_best
hardly_revolutionary
often_ineffective
perhaps_most
sometimes_satirical
usually_unconscious
especially_annoying
again_little
seriously_enough
yes
possibly_false
clearly_visible
often_terrible
perhaps_right
often_modern
basically_useless
never_socialist
definitely_related
definitely_true
hardly_moderate
sometimes_contradictory
maybe_third
often_disappointing
constantly_tight


In [112]:
[(k, counts[k]) for k in counts]

[('never', 13),
 ('rarely', 9),
 ('sometimes', 14),
 ('usually', 14),
 ('generally', 13),
 ('often', 13),
 ('already', 13),
 ('again', 6),
 ('constantly', 7),
 ('repeatedly', 5),
 ('frequently', 13),
 ('always', 13),
 ('maybe', 14),
 ('perhaps', 15),
 ('possibly', 14),
 ('probably', 12),
 ('really', 12),
 ('actually', 12),
 ('literally', 12),
 ('certainly', 14),
 ('truly', 15),
 ('obviously', 14),
 ('clearly', 15),
 ('definitely', 12),
 ('not', 13),
 ('almost', 12),
 ('basically', 15),
 ('hardly', 13),
 ('rather', 12),
 ('quite', 13),
 ('pretty', 11),
 ('very', 12),
 ('especially', 13),
 ('seriously', 13),
 ('completely', 13)]

In [98]:
# # this was just to find more examples for 'repeatedly'
# repeat = df['body'][df['body'].str.contains('repeatedly')]
# print(len(repeat))
# advs_sentences = {}
# for idx, i in enumerate(repeat):
#     print(idx)
#     doc = nlp(i)
#     for s_i, sentence in enumerate(doc.sentences):
#         words = [word.text for word in sentence.words]
#         adv = 'repeatedly'
#         if adv in words:
#             adv_idx = words.index(adv)

#             pos, text = get_head_pos(adv, sentence)
#             try:
#                 if pos =='ADJ' and words[adv_idx+1] == text:
#                     print(adv, text)
#                     print(sentence.text)

#                     # if we have combination already, add to examples
#                     if doc.sentences[s_i -1]:
#                         if adv + '_' + text in advs_sentences:
#                             advs_sentences[adv + '_' + text]['count']+=1
#                             advs_sentences[adv + '_' + text]['sentences'].append(doc.sentences[s_i -1].text
#                                                                                  + ' ' + sentence.text)
#                         else:
#                             advs_sentences[adv + '_' + text] = {'count' :1, 'sentences': 
#                                                                 [doc.sentences[s_i -1].text  
#                                                                  + ' ' + sentence.text]}
#             except exception:
#                 continue


885
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
repeatedly condescending
We're supposed to pretend that Mittens is a good guy who has not been repeatedly condescending about the 47%, women, and [many others](https://www.youtube.com/watch?v=pJWSIqv8NOc).
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
repeatedly enough
But they were stated loudly and repeatedly

In [107]:
# with open('adv_sent_final_5_to_15_adj.json', 'w') as fp:
#     json.dump(new_adv_sent, fp)

In [108]:
sent_json = 'adv_sent_final_5_to_15_adj.json'
with open(sent_json, 'r') as f:
    adv_sent_json = json.load(f)

In [113]:
len(adv_sent_json)

434

In [123]:
s = 'boo la yup'
w = s.split()
i = w.index('yup')
w[2] = 'bop'
w

['boo', 'la', 'bop']

In [155]:
# need to negate
new_adv_sent_neg = {}
errors = []
import re

for k in new_adv_sent:
    sentences = new_adv_sent[k]
    adv = k.split('_')[0]
    for s in sentences:
        new_sent = ''
        s = re.sub('\"|\*|\(|\)', '', s)
        print('POSITIVE')
        print(s)
        try: 
            words = s.split()
            adv_idx = words.index(adv)
#             print(adv_idx)
#             print(words[adv_idx-2:adv_idx+1])

            if adv not in ['not', 'never']:
                if words[adv_idx-1] == 'a':
                    words[adv_idx-1] = 'not'
                elif 'be' in words[adv_idx-1]:
                    words[adv_idx-1] = 'not'
                else:
                    words[adv_idx] = 'not'
            else:
                words[adv_idx] = 'totally'
            new_s = ' '.join(words)
            print('NEGATIVE')
            print(new_s)
            if k not in new_adv_sent_neg:
                new_adv_sent_neg[k] =[new_s]
            else:
                new_adv_sent_neg[k].append(new_s)

        except ValueError:
            errors.append(s)
            continue

POSITIVE
1. You're probably right that my post is mainly based on my feelings.
NEGATIVE
1. You're not right that my post is mainly based on my feelings.
POSITIVE
I think its better to look at it from the gaze of tribalism with a sectarian face. you're probably right, but i think sociological evidence and not theological evidence is more important for these kinds of claims.
NEGATIVE
I think its better to look at it from the gaze of tribalism with a sectarian face. you're not right, but i think sociological evidence and not theological evidence is more important for these kinds of claims.
POSITIVE
Too many countries believe this whole thing is a hiccup in history that everyone will forget about in a couple years. Other countries believe that doing more on the world stage to punish Russia will only make the starving dog of a country lash out even more and they're probably right.
NEGATIVE
Too many countries believe this whole thing is a hiccup in history that everyone will forget about in 

NEGATIVE
That poor confused man. I am not convinced that he is going to simultaneously and in equal parts, immensely benefit the world with his wealth and philanthropic activities; and harm it with his use of the state, along with its backward and archaic delivery methods for aid, investment, and welfare.
POSITIVE
You're crazy if you really think that and quite frankly, your moral paradigm is clearly no better than that of a psychopath. The idea that the killings don't matter because they could kill more and somehow that means the occupiers are being more humanitarian is just an incredibly stupid and obviously pro-genocidal argument.
NEGATIVE
You're crazy if you really think that and quite frankly, your moral paradigm is clearly no better than that of a psychopath. The idea that the killings don't matter because they could kill more and somehow that means the occupiers are being more humanitarian is just an incredibly stupid and not pro-genocidal argument.
POSITIVE
Sadly, the only one 

In [159]:
[(k, new_adv_sent[k]) for k in new_adv_sent if 'almost' in k]

[('almost_pointless',
  ["It's widely admitted that some corporations in particular pay a startlingly-low amount in US taxes. At the end of the day, for Americans it is almost pointless to theorize about optimal taxation, however, when we still have a political system in which there are only two parties, and both are dominated to varying degrees by the interests of capital."]),
 ('almost_zero',
  ['It will make Hillary **more** confident in her ability to win the nomination, and will remove pressure on her to take more clear stands on issues. Sanders has almost zero support and yet *he* is the one who is commanding the second-most press in the democratic race??',
   "What the fuck are you on about? Yeah, among the socialists it's a pretty great word, the rest of the country thinks it's a terrible concept with almost zero upside."]),
 ('almost_overwhelming',
  ['I have so much reading ahead of me, though. It&amp;#39;s almost overwhelming.']),
 ('almost_total',
  ["In countries that have

In [164]:
[(k, new_adv_sent) for k in new_adv_sent if 'probably' in k]

[('probably_right',
  {'probably_right': ["1. You're probably right that my post is mainly based on my feelings.",
    "I think its better to look at it from the gaze of tribalism with a sectarian face. you're probably right, but i think sociological evidence and not theological evidence is more important for these kinds of claims.",
    "Too many countries believe this whole thing is a hiccup in history that everyone will forget about in a couple years. Other countries believe that doing more on the world stage to punish Russia will only make the starving dog of a country lash out even more and they're probably right.",
    'I would imagine, for example, that there is far less organized crime in the U.K. than in Brazil, that they have a stronger mental health system, less corruption in the police force, etc. And you\'re probably right, But if you change "Brazil" to "The US" in that sentence, it still holds true.',
    "Haha. You're probably right."],
   'really_nice': ["yeah me too. I

In [139]:
errors

['On matters of policy, Ms. Lynch called capital punishment “an effective penalty” and said she disagreed with Mr. Obama’s statements that marijuana was no more harmful than alcohol. She called the National Security Agency’s collection of American phone records “certainly constitutional, and effective.”',
 '&gt; She called the National Security Agency’s collection of American phone records “certainly constitutional, and effective.”']

In [140]:
# with open('adv_sent_final_5_to_15_adj_neg.json', 'w') as fp:
#     json.dump(new_adv_sent_neg, fp)

In [67]:
# top_adj = {}
# for k in adv_counts:
#     m = max(adv_counts[k].values())
#     top_adj[k] = [(a, m) for a in adv_counts[k] if adv_counts[k][a] == m]

In [70]:
top_adj

{'probably': [('right', 7)],
 'really': [('good', 8)],
 'quite': [('clear', 3)],
 'pretty': [('sure', 29)],
 'not': [('sure', 73)],
 'usually': [('civil', 1),
  ('negative', 1),
  ('lovely', 1),
  ('visible', 1),
  ('right', 1),
  ('annoying', 1),
  ('wrong', 1)],
 'completely': [('different', 11)],
 'very': [('good', 25)],
 'truly': [('socialist', 2), ('great', 2), ('free', 2)],
 'never': [('good', 2)],
 'maybe': [('more', 1), ('unsustainable', 1), ('worse', 1), ('half', 1)],
 'always': [('true', 2), ('easy', 2), ('ideal', 2)],
 'rather': [('bad', 3)],
 'seriously': [('ill', 3)],
 'hardly': [('surprising', 2), ('liberal', 2)],
 'often': [('enough', 4)],
 'actually': [('able', 3)],
 'literally': [('impossible', 5)],
 'basically': [('nonsense', 1),
  ('worried', 1),
  ('impossible', 1),
  ('dead', 1),
  ('capitalist', 1)],
 'generally': [('non-toxic', 2)],
 'obviously': [('contrary', 2)],
 'certainly': [('cruel', 1),
  ('poor', 1),
  ('constitutional', 1),
  ('fungible', 1),
  ('reasona

In [323]:
# dir(sentence)

In [21]:
{k: v for k, v in sorted(adv_counts.items(), key=lambda item: item[1], reverse=True)}

{'not': 981,
 'more': 760,
 'very': 597,
 'so': 486,
 'pretty': 328,
 'as': 315,
 'just': 306,
 'most': 282,
 'too': 238,
 'really': 221,
 'much': 218,
 'all': 191,
 'less': 186,
 'even': 150,
 'completely': 97,
 'enough': 88,
 'actually': 85,
 'way': 82,
 'only': 80,
 'extremely': 78,
 'far': 74,
 'quite': 69,
 'probably': 65,
 'about': 65,
 'absolutely': 63,
 'relatively': 58,
 'always': 55,
 'little': 53,
 'rather': 53,
 'totally': 52,
 'perfectly': 51,
 'incredibly': 49,
 'simply': 47,
 'no': 43,
 'entirely': 42,
 'fairly': 40,
 'right': 39,
 'highly': 39,
 'well': 39,
 'inherently': 35,
 'never': 34,
 'mostly': 31,
 'least': 30,
 'super': 30,
 'almost': 30,
 'somewhat': 29,
 'particularly': 29,
 'truly': 28,
 'obviously': 28,
 'ever': 26,
 'deeply': 26,
 'already': 26,
 'exactly': 26,
 'certainly': 24,
 'slightly': 23,
 'generally': 22,
 'equally': 22,
 'fundamentally': 21,
 'literally': 21,
 'clearly': 21,
 'often': 20,
 'especially': 20,
 'indeed': 19,
 'sometimes': 19,
 'remote

In [22]:
{k: v for k, v in sorted(adj_counts.items(), key=lambda item: item[1], reverse=True)}

{'sure': 200,
 'good': 145,
 'bad': 133,
 'different': 124,
 'important': 110,
 'better': 109,
 'true': 107,
 'likely': 100,
 'wrong': 97,
 'able': 79,
 'possible': 75,
 'high': 68,
 'hard': 66,
 'clear': 64,
 'enough': 62,
 'stupid': 60,
 'easy': 59,
 'difficult': 56,
 'right': 53,
 'less': 51,
 'worse': 51,
 'same': 49,
 'great': 48,
 'efficient': 47,
 'effective': 47,
 'little': 47,
 'simple': 46,
 'conservative': 42,
 'close': 42,
 'low': 39,
 'powerful': 37,
 'interested': 37,
 'fine': 36,
 'common': 36,
 'lower': 35,
 'dangerous': 35,
 'concerned': 35,
 'accurate': 35,
 'valuable': 35,
 'higher': 34,
 'large': 34,
 'similar': 34,
 'obvious': 33,
 'worth': 33,
 'aware': 32,
 'productive': 32,
 'liberal': 32,
 'expensive': 31,
 'familiar': 31,
 'interesting': 31,
 'relevant': 31,
 'impossible': 30,
 'useful': 30,
 'free': 30,
 'poor': 29,
 'fair': 29,
 'few': 29,
 'small': 29,
 'big': 29,
 'racist': 28,
 'successful': 26,
 'specific': 26,
 'violent': 26,
 'easier': 25,
 'correct': 

In [23]:
# import pandas as pd 
# df_adv = pd.DataFrame.from_dict(advs_sentences, orient='index')

In [24]:
# df_adv

0    \
probably_right             [You're probably right](http://www.kansascity....   
really_blatant             hard to believe they are really that blatant l...   
not_obvious                I'm not sure, however, why this wouldn't be ob...   
so_nice                    I'm first generation American as well and part...   
really_nice                I'm first generation American as well and part...   
quite_grateful             We are quite grateful to live in America, whic...   
as_expensive               Keep in mind I live in Canada where alcohol is...   
pretty_expensive           Higher alcohol taxes do price poor people out ...   
generally_expensive        Higher alcohol taxes do price poor people out ...   
not_convinced              So what I'm saying is I'm not convinced of the...   
so_unfair                  Maybe he's one of those who can't seem to foll...   
pretty_nice                The police then called EMS and were, at least ...   
too_high                         There is no standard too high for a leader.   
as_flawed                  If a leader would like to be judged as flawed,...   
no_less                               Those in power expect no less from us.   
as_cartoonish              Stuff like that is why libertarians are seen a...   
least_minimum              If the waiter doesn't make at least minimum wa...   
pretty_generous            Personally I was thinking 5 days in jail to ge...   
not_ineffective            Am I just not managing to think of any evidenc...   
just_gruntled                          Why isn't anybody ever just gruntled?   
ever_gruntled                          Why isn't anybody ever just gruntled?   
too_tired                    Come on guys, we are all too tired for war now.   
all_tired                    Come on guys, we are all too tired for war now.   
right_afraid               The right is afraid that someone, somewhere, i...   
so_inaccurate              Though I still think thats a bit off target be...   
more_powerful              Though I still think thats a bit off target be...   
somewhat_inaccurate        Though I still think thats a bit off target be...   
usually_civil                                           It is usually civil.   
enough_generous            If a restaurant, or any business for that matt...   
so_competitive             Increased Immigration along with Free Trade Ag...   
...                                                                      ...   
most_political             The Right in America is certainly not anti hie...   
incredibly_strict          Should have pointed him to the Detroit gun ban...   
extremely_detrimental      And if it does it'll be so loaded with pork an...   
literally_necessary        Regardless, unless it's literally biologically...   
enough_realistic           I'm not anti-capitalism, but I'm realistic eno...   
virtually_unknown             Because reddit is virtually unknown in Israel.   
least_able                 Typically the least able to dodge are the smal...   
well_run                   No incentives for a well-run government, only ...   
least_fundamental          Read something at least fundamental on the sub...   
absolutely_confident       “Despite the fact that there are differences i...   
inherently_social          Marxian value is inherently social and there i...   
so_inconvenient            I link a KPMG table elsewhere, but it is easy ...   
really_funny               And it's really funny how the Assad regime did...   
right_radical              &gt;But, I suspect that most people who work f...   
fairly_radical             &gt;But, I suspect that most people who work f...   
not_stable                 If a nation is running a trade deficit, then e...   
honestly_old               Keep an eagle eye on your kids until they're 1...   
just_open                  You don't need to terrorize them, just be open...   
almost_intolerable         In most countries in the world, the left is as

In [27]:
# df_adv.to_csv('/Users/isabellelorge/Desktop/reddit_project/df_adv.csv')

In [104]:
import gensim.downloader as api

word_vectors = api.load("glove-wiki-gigaword-100")  # load pre-trained word-vectors from gensim-data

In [122]:
# Check the "most similar words", using the default "cosine similarity" measure.
result = word_vectors.most_similar(positive=['very', 'extremely', 'utterly'], topn = 100)
#                                    negative=['otherwise', 'be'], topn = 100)
result

[('quite', 0.8944221138954163),
 ('incredibly', 0.8598204255104065),
 ('equally', 0.8386393189430237),
 ('pretty', 0.8132274150848389),
 ('too', 0.8111996650695801),
 ('absolutely', 0.805686354637146),
 ('fairly', 0.803045392036438),
 ('so', 0.7896586060523987),
 ('extraordinarily', 0.7764715552330017),
 ('particularly', 0.7705060243606567),
 ('totally', 0.7679736018180847),
 ('otherwise', 0.7633854150772095),
 ('difficult', 0.7632368803024292),
 ('surprisingly', 0.7611854672431946),
 ('similarly', 0.7601125240325928),
 ('obviously', 0.7571256756782532),
 ('seems', 0.7558939456939697),
 ('kind', 0.7518400549888611),
 ('highly', 0.7510290145874023),
 ('relatively', 0.7507774233818054),
 ('nothing', 0.749722957611084),
 ('exceedingly', 0.7460922002792358),
 ('something', 0.7446709275245667),
 ('truly', 0.7406541109085083),
 ('rather', 0.7384292483329773),
 ('somewhat', 0.7373349666595459),
 ('especially', 0.7370266318321228),
 ('less', 0.7361097931861877),
 ('really', 0.7359302639961243)

In [141]:
result = word_vectors.most_similar(positive=['brilliant'], topn = 100)
#                                negative=['otherwise', 'be'], topn = 100)
result

[('superb', 0.8146100640296936),
 ('dazzling', 0.7594192624092102),
 ('clever', 0.6981667876243591),
 ('impressive', 0.6959413290023804),
 ('terrific', 0.6958699226379395),
 ('spectacular', 0.6881232261657715),
 ('amazing', 0.6854714751243591),
 ('perfect', 0.6846548914909363),
 ('stunning', 0.6824212074279785),
 ('splendid', 0.6761254072189331),
 ('beautiful', 0.6755616068840027),
 ('wonderful', 0.6738944053649902),
 ('masterful', 0.6727157235145569),
 ('remarkable', 0.671766996383667),
 ('fantastic', 0.6641409993171692),
 ('brilliantly', 0.6628473401069641),
 ('excellent', 0.6624909043312073),
 ('magnificent', 0.6592804789543152),
 ('imaginative', 0.6387056708335876),
 ('gorgeous', 0.6375812292098999),
 ('memorable', 0.6371219158172607),
 ('brave', 0.6339940428733826),
 ('delightful', 0.6305860877037048),
 ('best', 0.6288588643074036),
 ('bright', 0.6285106539726257),
 ('accomplished', 0.6283156275749207),
 ('talented', 0.6273253560066223),
 ('gutsy', 0.6273004412651062),
 ('daring',

In [157]:
vector_adv = word_vectors['utterly']
vector_adj = word_vectors['brilliant']
vector = vector_adv + vector_adj
vector_mult = vector_adv * vector_adj
vector_adv1 = word_vectors['extremely']
vector_adj1 = word_vectors['intelligent']
vector1 = vector_adv1 + vector_adj1
vector1_mult = vector_adv1 * vector_adj1
vector_adv2 = word_vectors['barely']
vector_adj2 = word_vectors['blue']
vector2 = vector_adv2 + vector_adj2
vector2_mult = vector_adv2 * vector_adj2

In [161]:
kron_vector = np.kron(vector_adv, vector_adj)
kron_vector1 = np.kron(vector_adv1, vector_adj1)
kron_vector2 = np.kron(vector_adv2, vector_adj2)

In [163]:
kron_vector.shape

(10000,)

In [153]:
word_vectors.n_similarity(['utterly', 'brilliant'], ['extremely', 'intelligent'])

0.6592066

In [151]:
from scipy.spatial import distance
1-distance.cosine(vector, vector1)

0.659206748008728

In [158]:
1-distance.cosine(vector, vector2)

0.3541416823863983

In [156]:
1-distance.cosine(vector_mult, vector1_mult)

0.5760245323181152

In [159]:
1-distance.cosine(vector_mult, vector2_mult)

0.5549370646476746

In [165]:
1-distance.cosine(kron_vector, kron_vector1)

0.2523985505104065

In [164]:
1-distance.cosine(kron_vector, kron_vector2)

0.1028696820139885

In [166]:
word_vectors.n_similarity(['very', 'sad'], ['very', 'happy'])

0.90755343

In [170]:
word_vectors.n_similarity(['very', 'sad'], ['not', 'miserable'])

0.76420575

In [168]:
word_vectors.n_similarity(['very', 'sad'], ['extremely', 'happy'])

0.89391166

In [167]:
word_vectors.n_similarity(['sad'], ['happy'])

0.6801137

In [171]:
import tensorflow as tf
